# Кластеризация и характеристика обращений клиентов

In [1]:
import os
import warnings
import logging

import pandas as pd
import numpy as np
import plotly.io as pio

import transformers
import torch

from sql_connect import read_sql
from text_conversion import summarization, get_summary, clean_text
from text_vectorization import Embedder
from clusterization import get_clusters, generate_topics, plot_clusters

from sklearn.metrics import silhouette_score, davies_bouldin_score
from sklearn.cluster import KMeans
from openai import OpenAI

warnings.filterwarnings("ignore", category=UserWarning)
pd.set_option('display.max_colwidth', None)
transformers.tokenization_utils.logger.setLevel(logging.ERROR)
transformers.configuration_utils.logger.setLevel(logging.ERROR)
transformers.modeling_utils.logger.setLevel(logging.ERROR)
pio.renderers.default = "notebook_connected"

SEED = 654122

In [2]:
calls_query = '''
SELECT TOP 5 *
FROM calls
WHERE CAST(call_date AS DATE) BETWEEN '2024-02-15' AND '2024-02-15';
'''

In [3]:
calls = read_sql(calls_query)
calls.drop('address',  axis=1)

id           call_date     ak   miko    mrm  incoming  \
0  9496291 2024-02-15 05:49:28   True  False   True     False   
1  9496292 2024-02-15 06:00:28  False   True  False      True   
2  9496293 2024-02-15 06:09:37   True  False   True     False   
3  9496294 2024-02-15 06:09:47  False   True  False      True   
4  9496295 2024-02-15 06:13:33   True  False   True     False   

                                                                                                                                                                                                                                                          linkedid  \
0  1707965367.24765302                                                                                                                                                                                                                                               
1  1707966019.16732091                                                                                                                                                                                                                                               
2  1707966576.24765318                                                                                                                                                                                                                                               
3  1707966579.16732093                                                                                                                                                                                                                                               
4  1707966813.24765340                                                                                                                                                                                                                                               

                                                                                                                                                                                                                                                              oper  \
0  МРМ                                                                                                                                                                                                                                                               
1  Оператор_056                                                                                                                                                                                                                                                      
2  МРМ                                                                                                                                                                                                                                                               
3  Оператор_015                                                                                                                                                                                                                                                      
4  МРМ                                                                                                                                                                                                                                                               

                                                                                                                                                                                                                                                         base_name  \
0  1C_Service_NNOV                                                                                                                                                                                               

In [4]:
tr_query = '''
SELECT TOP 5 *
FROM transcribations
WHERE CAST(record_date AS DATE) BETWEEN '2024-02-15' AND '2024-02-15';
'''

In [5]:
transcribations = read_sql(tr_query)
transcribations.T

0  \
transcribation_date                     2024-02-15 03:39:37   
date_y                                                 None   
date_m                                                 None   
date_d                                                 None   
side                                                  False   
text                                 Продолжение следует...   
start                                                  0.33   
audio_file_name      in_5056_2024-02-15-03-28-42rxtx-in.wav   
conf                                                  0.885   
end_time                                              30.25   
sentiment                                              None   
sentiment_pos                                          None   
sentiment_neg                                          None   
ID                                                173033615   
linkedid                                1707956919.16731963   
dst                                                    main   
record_date                             2024-02-15 03:28:42   
source_id                                                 1   
src                                                    5056   
cpu_id                                                    0   
duration                                              46.54   
file_size                                            744684   
queue_date                              2024-02-15 03:39:29   
model                                                     1   

                                                          1  \
transcribation_date                     2024-02-15 03:39:37   
date_y                                                 None   
date_m                                                 None   
date_d                                                 None   
side                                                  False   
text                                                  Алло?   
start                                                 32.31   
audio_file_name      in_5056_2024-02-15-03-28-42rxtx-in.wav   
conf                                                  0.354   
end_time                                              33.31   
sentiment                                              None   
sentiment_pos                                          None   
sentiment_neg                                          None   
ID                                                173033616   
linkedid                                1707956919.16731963   
dst                                                    main   
record_date                             2024-02-15 03:28:42   
source_id                                                 1   
src                                                    5056   
cpu_id                                                    0   
duration                                              46.54   
file_size                                            744684   
queue_date                              2024-02-15 03:39:29   
model                                                     1   

                                                          2  \
transcribation_date                     2024-02-15 03:39:37   
date_y                                                 None   
date_m                                                 None   
date_d                                                 None   
side                                                  False   
text                                                  Алло?   
start                                                 39.93   
audio_file_name      in_5056_2024-02-15-03-28-42rxtx-in.wav   
conf                                                  0.508   
end_time                                              40.21   
sentiment                                              None   
sentiment_pos                                          None   
sentiment_neg                                          None   
ID                      

In [6]:
query = '''
SELECT DISTINCT
       start,
       record_date,
       linkedid,
       audio_file_name,
       model,
       text,
       side,
       src,
       dst
FROM transcribations
WHERE linkedid IN (SELECT DISTINCT
                          linkedid
                   FROM transcribations
                   WHERE CAST(record_date AS DATE) BETWEEN '2024-02-07' AND '2024-02-15'
                       AND model=1)
    AND ((side='True' AND LEN(src)=4 AND dst NOT LIKE '[0-9][0-9][0-9][0-9]')
         OR (side='False' AND LEN(src)>4 AND dst LIKE '[0-9][0-9][0-9][0-9]')
         OR (side='True' AND LEN(src)>4 AND LEN(dst)>4))
    AND text IS NOT NULL AND text <> ''
ORDER BY start;
'''

In [7]:
df = read_sql(query)
df = df.drop(columns=['start']).drop_duplicates()
df.sample(5, random_state=SEED).drop(columns=['src', 'dst'])

record_date             linkedid  \
10647 2024-02-09 14:08:58  1707476937.16549073   
73153 2024-02-15 18:01:03  1708009262.16760199   
33351 2024-02-13 15:40:53  1707828051.16684498   
91866 2024-02-08 14:21:27  1707391286.16515608   
19112 2024-02-12 17:17:35  1707747455.24701639   

                                                                     audio_file_name  \
10647                                  in_79264924612_2024-02-09-14-08-58rxtx-in.wav   
73153                                   in_4992000746_2024-02-15-18-01-03rxtx-in.wav   
33351                                        in_5077_2024-02-13-15-40-53rxtx-out.wav   
91866                                  in_79647289580_2024-02-08-14-21-27rxtx-in.wav   
19112  a2024-02-12t17:17:35b_c9933426614d_e9852223343f_g1707747455.24701639h-out.wav   

       model  \
10647      0   
73153      0   
33351      0   
91866      0   
19112      0   

                                                                                       text  \
10647  в холодильнике компрессора у нас отдельный компрессор два компьютера на холодильнике   
73153                         а вот на назавтра можно заказать чтобы завтра да на завтра да   
33351                                                                         а потом фирма   
91866                                                             аварийное вскрытие дверей   
19112                                                                                   ага   

        side  
10647  False  
73153  False  
33351   True  
91866  False  
19112   True

In [8]:
df.to_csv('calls_transcripts.csv', index=False)
df = pd.read_csv(
    'calls_transcripts.csv',
    parse_dates=[0],
    dtype={'linkedid': 'object'}
)

In [9]:
summarized = summarization(
    df,
    [
       'linkedid',
       'audio_file_name',
       'record_date',
       'model',
       'side',
       'src',
       'dst'
    ],
    'text',
    'продолжение следует',
    r'\.{2,}'
)

In [10]:
summarized['text_length'] = summarized['text'].apply(len)
summarized = summarized[summarized['text_length'] >= 50]
summarized = summarized.sort_values(by=['linkedid', 'record_date']).drop_duplicates(subset='linkedid').reset_index(drop=True)

summarized.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8103 entries, 0 to 8102
Data columns (total 9 columns):
 #   Column           Non-Null Count  Dtype         
---  ------           --------------  -----         
 0   linkedid         8103 non-null   object        
 1   audio_file_name  8103 non-null   object        
 2   record_date      8103 non-null   datetime64[ns]
 3   model            8103 non-null   int64         
 4   side             8103 non-null   bool          
 5   src              8103 non-null   object        
 6   dst              8103 non-null   object        
 7   text             8103 non-null   object        
 8   text_length      8103 non-null   int64         
dtypes: bool(1), datetime64[ns](1), int64(2), object(5)
memory usage: 514.5+ KB


In [11]:
summarized.to_csv('summarized_transcripts.csv', index=False)
summarized = pd.read_csv(
    'summarized_transcripts.csv',
    parse_dates=[2],
    dtype={'linkedid': 'object'}
)

In [13]:
summary = pd.DataFrame()
summary[['linkedid', 'text']] = summarized[['linkedid', 'text']]

client = OpenAI(api_key=os.environ.get("OPENAI_API_KEY", ""))
summary = get_summary(summary, client, seed=SEED)
summary[['text', 'result']].sample(5, random_state=SEED)

text  \
1458                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                елена, добрый день.  алло.  вы не могли меня связать с клиентом, но заявка 1-49-8-41.  2-1-4-9-8-4-1.  да, это вопрос.  алло, день добрый.  ага.  это вот по поводу ремонта холодильника.  да.  нет.  да, значит, смотрите, берем и выправляем температуру побольше.  давайте, давайте, давайте.  а с чего вы взяли, что у вас внизу 27?  27 градусов, это морозилка.  27 градусов, это морозилка или холодильник?  да, но прибавляйте температуру.  там на нем есть кнопочки.  его полностью нет кнопочек, надо поднять температуру, и все.  да, не смогу.  ага, ага, ага.  ну, давай, я вам ширком заеду, нормально будет?  все, если 7-8, нормально?  все, я вам заеду вниз.  я понял, я понял.  хорошо, ладно, я там приеду.  сегодня, сегодня буду.  давайте, давайте.   
3013                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  а да говорите пожалуйста погромче да да надо да конечно мастера а но когда пробегают хоть на холодильник выгружать можем да в общем её вода вот так вот то спасибо андрей аллея вам мы ждём она побыстрее   
7568                                                                                                  алло, здравствуйте. я звонила, полдвенадцатого, наверное, время было, по поводу мастера по телевизору. сказали, что в течение часа перезвонит. время уже три часа, никто не звонит. нет, не установлен. могут, могут. я сама их сбрасываю.  улица нагулинская, 59 иодом. да? вот не знаю, вот я говорю вам, что я ждала, ждала. сейчас сын звонит, говорит, мам, мне что, приезжать, не приезжать? я говорю, мне никто не дозвонился. я говорю, сейчас будут так, повторно звонить. ну, все, ладно, я жду, что тут рассуждать. хорошо? хорошо.  алло. здравствуйте.  здравствуйте. мне нужно переключить телевизор. у меня была там, это, ннтв, это, коробка, это какая-то тарелка. мне нужно сделать этот, как его, ну, на наши девятнадцать каналов. да, да. ну, конечно, не первой свежести. уж лет пятнадцать это. я все купила, у меня есть приставка.  да, антенна. но у меня антенна разводка по дому.  да? нет, у меня обыкновенная. но тарелка у меня есть. потому что на первом этаже у меня столов. а на втором я хочу, чтобы у меня просто наше было нижегородское телевидение.  хорошо, подъезжайте. вы мне скажите, сколько примерно услуга-то стоит?  все, ладно, хорошо.  я буду ждать. все, до свидания.   
7591                                                                                                                                           

In [14]:
summary.to_csv('summary.csv', index=False)
summary = pd.read_csv(
    'summary.csv',
    dtype={'linkedid': 'object'}
)

In [15]:
clean = clean_text(
    summary,
    'нет ключевой информации|не удалось выделить ключевую информацию|никакого разговора не состоялось',
    'адрес|город|метро|дом|квартир|подъезд|домофон|этаж|мой телефон|наш телефон|мой номер|номер телефона|номер заявки|номер заказа|телефон для связи|контактный номер|контактный телефон|спасибо|до свидания',
    r'[а-яА-ЯёЁ]'
)
clean['text'].to_frame().sample(10, random_state=SEED)

text
5183                                  У меня есть рекламная бумажка с номером 148.
3068     У нас также проблема с холодильником, можно к вам подъехать и посмотреть?
6072       Не реагирует кнопка старта, как будто что-то отлетело внутри механизма.
1735                                                 Какие предельные сроки у вас?
7821                         Заказ платного мастера для уточнения времени прихода.
386                                             Сколько это будет стоить примерно?
1269  Наверное, это 32-р-л-р, английская, л-л-л, тоже большая английская, 933-р-б.
1672                                                               С этого номера?
3357                               Непонятно, почему мастер так долго не приходит.
7321                    Сориентируйтесь по цене, сколько там, вызов стоит мастера?

In [16]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model_name = 'cointegrated/rubert-tiny2'

embedder = Embedder(model_name, device)
embeddings = embedder.get_embeddings(clean, 512)
embeddings.tail()

Processing batches:   0%|          | 0/19 [00:00<?, ?it/s]

linkedid  \
9493  1708026084.16765862   
9494  1708026084.16765862   
9495  1708026084.16765862   
9496  1708026084.16765862   
9497  1708026084.16765862   

                                                                   text  \
9493  Машина перестала работать, мотор шумел, сейчас отключена от сети.   
9494                                         Сколько стоит диагностика?   
9495                        Когда-то нужно будет договориться о визите.   
9496                   Если мотор сломался, то гарантия действует, так?   
9497                               У меня есть документы, чек и прочее.   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              embedding  
9493        [-0.4979679, -0.16442797, 0.36842173, -1.676214, 0.3559669, 0.19501455, -0.42754954, -0.94375217, 0.71071756, 0.011492193, 0.3678645, 0.45247632, 0.5550098, 0.8986785, -0.37330252, -0.6497234, 0.6455413, -0.023895614, -0.61900723, -0.79517746, -0.095056355, 0.9744611, 0.13928863, -0.26286507, 0.85038006, 0.27458072, 0.5151521, 0.019576043, -0.033802614, 0.71436477, -0.38502896, -0.09489034, -0.05438745, -0.10605653, 0.37437785, 0.58846146, 0.014951134, -0.68956316, 0.4838717, -0.12497558, 0.630146, 0.4168074, 0.34916487, -0.34569946, 0.5091611, 0.15328164, -0.37202215, 1.0042703, 0.09382937, -0.16301294, -0.34029534, 0.07011742, -0.07011939, -0.3813418, 0.17086992, -0.26923758, 0.65138745, 0.044585854, 0.032859582, -0.10529827, 0.4048554, 0.3378154, 1.0203592, -0.7453835, 0.71147454, -0.7332988, 0.2426767, 0.2388079, 0.3004897, -0.26576555, 1.1265013, 0.35250518, -0.47162372, -0.8783016, 0.40011892, -0.8526208, 0.008848876, -0.4220984, 0.15422377, 0.27740133, -0.02472756, -0.060771517, 0.085469306, 0.39651388, -0.26952672, -0.6925851, -0.99020034, 0.38377187, -0.21832691, -0.56522065, 0.94754934, -0.22286668, 0.44678244, -0.21607503, 0.8348493, 0.31849736, 0.42448932, 0.19199519, 0.17139351, -0.1333192, ...]  
9494                [-0.056837603, -0.12828873, -0.33625045, -1.046955, -0.742052, -0.19488113, 0.22727776, -0.24017954, -0.29870102, 0.15916987, 0.19967127, -0.38493606, 0.1942632, 1.7492805, -0.51252276, -0.2938362, 0.67394114, 0.9360674, -0.02574356, 0.30983338, -0.2890269, 0.093564965, 0.06499841, 0.41844738, 1.7331647, -0.1167899, 0.28999856, 1.002111, 1.0973669, 0.31991345, 0.6112205, 0.6071232, -0.58056813, -0.09902742, 0.20809667, 0.2317399, 0.8121771, -0.66393685, -0.33162472, -0.050684024, 0.52022207, -0.4664117, 0.00070955855, -0.48104763, 0.35467634, -0.38893127, -0.2684473, -0.64813644, 0.8216538, 0.57753295, 0.7762627, -0.13106127, 0.126467, -0.803066, 0.31932488, 0.020890161, 0.9325392, -0.012108277, -0.17315097, 0.13772224, 0.5116455, 0.6035383, -0.5713238, -0.07231391, 0.70880765, -0.32310212, 0.19457988, 0.059459537, 0.008304007, 0.812063, -0.33621076, 0.032670736, -0.10099611

In [17]:
embeddings.to_pickle("embeddings.pkl")
embeddings = pd.read_pickle('embeddings.pkl')

In [18]:
matrix = np.stack(embeddings.embedding.values)

best_silhouette_score = -1
best_db_index = np.inf
best_count = None
silhouette_scores = []
db_indexes = []
cluster_sizes_list = []

for count in range(4, 20):
    clusterer = KMeans(
        n_clusters=count,
        max_iter=100,
        init='random',
        n_init=10,
        random_state=SEED,
        algorithm='lloyd'
    )
    clusterer.fit(matrix)
    labels = clusterer.labels_

    cluster_sizes = np.bincount(labels[labels >= 0])
    cluster_sizes_list.append((count, cluster_sizes))
    
    if len(set(labels)) > 1:
        silhouette = silhouette_score(matrix, labels)
        db_index = davies_bouldin_score(matrix, labels)
        
        silhouette_scores.append((count, silhouette))
        db_indexes.append((count, db_index))
        
        if silhouette > best_silhouette_score:
            best_silhouette_score = silhouette
            best_count = count
        
        if db_index < best_db_index:
            best_db_index = db_index
            best_count_db = count

for count, cluster_sizes in cluster_sizes_list:
    print(f"Количество кластеров={count}, размеры кластеров: {cluster_sizes}")

print(
    "Лучшее количество кластеров по силуэту:",
    best_count,
    "с оценкой силуэта:",
    best_silhouette_score
)
print(
    "Лучшее количество кластеров по Davies-Bouldin:",
    best_count_db,
    "с индексом Davies-Bouldin:",
    best_db_index
)

Количество кластеров=4, размеры кластеров: [3009 2525  832 3132]
Количество кластеров=5, размеры кластеров: [2624 2046 2189 1915  724]
Количество кластеров=6, размеры кластеров: [2053  716 1632 1823 2128 1146]
Количество кластеров=7, размеры кластеров: [1148 1550 1226  663 1948 1699 1264]
Количество кластеров=8, размеры кластеров: [ 786  651 1781 1260 1172 1188 1084 1576]
Количество кластеров=9, размеры кластеров: [ 551 1345  963 1126  898 1716 1171  763  965]
Количество кластеров=10, размеры кластеров: [1123 1216 1195  524  894 1193  867  983  751  752]
Количество кластеров=11, размеры кластеров: [ 670  977  843 1183  642  941  892  557 1001 1085  707]
Количество кластеров=12, размеры кластеров: [1007  384  515  768 1054  633  538  709 1079 1074  985  752]
Количество кластеров=13, размеры кластеров: [ 671  785  483  979  728  741  884  893  493  967  369  475 1030]
Количество кластеров=14, размеры кластеров: [906 810 890 924 505 507 452 352 719 392 607 762 728 944]
Количество кластеро

In [19]:
embeddings['general_cluster'] = get_clusters(matrix, 4, seed=SEED)
embeddings['detail_cluster'] = get_clusters(matrix, 17, seed=SEED)
embeddings.sample(5, random_state=SEED)

linkedid  \
5183  1707818656.16675625   
3068  1707724891.16628990   
6072  1707840665.24735398   
1735  1707480505.16552741   
7821  1707928183.16729557   

                                                                           text  \
5183                               У меня есть рекламная бумажка с номером 148.   
3068  У нас также проблема с холодильником, можно к вам подъехать и посмотреть?   
6072    Не реагирует кнопка старта, как будто что-то отлетело внутри механизма.   
1735                                              Какие предельные сроки у вас?   
7821                      Заказ платного мастера для уточнения времени прихода.   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    embedding  \
5183                  [0.34172028, -0.33629414, -0.1097159, -1.247525, -0.27990633, 0.51260847, -0.63870245, -0.11136607, -0.4875047, 0.32284248, -0.16470568, 0.015203402, 0.018587593, 0.6370268, 0.0340221, -0.8446673, 0.98979795, -0.4644983, -0.35859728, 0.26823002, -0.058247466, 0.6324061, -0.16675235, -0.6370207, 1.0574945, 0.10695886, 0.021141259, 0.22079886, -0.30686513, 0.34525856, -0.287101, 0.18440305, 0.13792707, 0.11609897, -0.7952391, 0.49511096, 0.75084454, -0.67153275, 0.72402984, -0.15713343, -0.5967252, -0.6107762, 0.210044, -0.3394725, -0.101243064, 0.07740026, 0.17367887, 0.5916466, -0.07471143, -0.8263201, 0.19900964, 0.09298143, -0.7747403, 0.5351638, -0.5600426, 0.27307212, 0.22436999, 0.80142754, 0.8677571, -0.3782203, -0.74352413, 0.26979864, 0.2651819, -0.42189372, -0.015804779, 0.7365855, 0.10800081, -0.36456314, 0.08245278, -0.34876233, -0.18687557, 0.26697809, 0.5455688, -0.63352746, -0.24016371, -1.1038413, -0.73003876, 0.30577105, 0.76436806, -0.14990714, -0.41612893, 0.12068767, -0.23495033, 0.052044593, 0.3622946, -0.267436, 0.17798154, 0.18006182, 0.03196864, 0.23106247, 0.31619182, -0.8505343, 1.4209718, -0.003948184, -0.3130358, 0.32516816, 0.07216576, 0.85801977, 0.08876961, -0.37254053, ...]   
3068                      [0.2545006, 0.1392384, -0.054480083, -1.4121215, -0.09274582, 0.9975856, -0.052353095, -0.52341133, -0.78428787, 0.5405477, -0.8818014, -0.469159, 0.38717964, 0.33622438, -0.5416208, -0.38187993, 0.4157743, 0.36083114, -0.22107404, -0.12873429, -0.5253635, 0.08635603, 0.19520551, -0.55480385, 1.8263806, 0.065083295, -0.6654921, 1.1063515, -0.6112403, 0.334479, 0.82683605, 0.21771508, -0.038728278, -0.26941168, -0.25802484, 0.33969948, 0.54871833, 0.18667474, 0.6995224, 0.39487487, 0.5335936, -0.091959424, 1.393002, -0.49528667, -0.07670755, -0.30062, 0.06625104, 0.3597671, -0.53423, -0.104656234, -0.04322321, -0.5818323, -0.4042913, -0.4376722, -0.5309976, 0.21567959, 0.7918464, -0.39007145, 0.087813705, -0.062349055, 0.48030698, 0.98740166, 0.27570474, -0.23271926, 0.51015127, -0.08265654, -0.9172821, -0.23

In [20]:
embeddings.to_pickle("clustered_transcripts.pkl")
embeddings = pd.read_pickle('clustered_transcripts.pkl')

In [21]:
general_topics = generate_topics(
    client,
    embeddings,
    'general_cluster',
    matrix,
    4,
    150,
    seed=SEED
)
detail_topics = generate_topics(
    client,
    embeddings,
    'detail_cluster',
    matrix,
    17,
    35,
    seed=SEED
)
display(general_topics, detail_topics)

{0: 'Проблема с оказанными услугами',
 1: 'Запрос на вызов и уточнение информации о времени и услугах',
 2: 'Запрос на цену и оценку стоимости ремонта',
 3: 'Просьба о прозвоне, уточнение деталей и контактов'}

{0: 'Вопросы о стоимости и оплате услуг',
 1: 'Запросы о способах и возможностях связаться с мастером',
 2: 'Уточнение местоположения проблемы и требуемых услуг',
 3: 'Запросы о времени и сроках приезда мастера',
 4: 'Запросы о конкретных проблемах с бытовой техникой',
 5: 'Озвучивание проблем и запросы о возможных вариантах решения',
 6: 'Неудовлетворенность качеством предоставленных услуг и запросы на прекращение сотрудничества',
 7: 'Вопросы о сроках, времени и деталях визита мастера',
 8: 'Запросы о наличии запчастей и техники, а также о ценах',
 9: 'Вопросы о предоставлении квитанций, возможности отмены вызова и других дополнительных услугах',
 10: 'Запросы на уточнение стоимости услуг и консультаций',
 11: 'Запросы на перенос визита и другие подобные запросы',
 12: 'Запросы на вызов мастера и уточнение возможности ремонта',
 13: 'Уточнение проблем с бытовой техникой и запросы на ремонт',
 14: 'Запросы на быстрый приезд мастера и оказание услуг',
 15: 'Запросы на уточнение подробн

In [22]:
embeddings['edited_cluster'] = embeddings['detail_cluster'].replace(
    {10: 0, 3: 7, 4: 13, 5: 13, 15: 13}
)
keys = [3, 4, 5, 10, 15]
edited_topics = {k: v for k, v in detail_topics.items() if k not in keys}

In [23]:
fig = plot_clusters(
    'Общие категории обращений',
    embeddings,
    'general_cluster',
    general_topics,
    36,
    30
)
fig.show()

In [24]:
fig = plot_clusters(
    'Детальные категории обращений',
    embeddings,
    'edited_cluster',
    edited_topics,
    36,
    24
)
fig.show()